# FabLog Data Visualisation

Visualisation for 210625 fab log data


In [14]:
LOG_PATH = "..\\FabLogs"
import os
file_names = os.listdir(LOG_PATH)
print(file_names)

['S01_0.txt', 'S01_1.txt', 'S01_2.txt', 'S01_3.txt', 'S01_4.txt', 'S01_5.txt', 'S01_6.txt', 'S01_7.txt', 'S01_8.txt', 'S01_9.txt']


## 1: Basic Log Data

In [65]:
%matplotlib inline
import numpy as np
import pandas as pd
import math
import matplotlib.pyplot as plt
import plotly.express as px
from datetime import datetime, timedelta
import plotly.io as pio
pio.renderers.default = "plotly_mimetype+notebook_connected"
pd.options.plotting.backend = "plotly"

def string_to_datetime(string):
    day, month, year, hour, minute, second = [int(t) for t in string.split(';')[1:-1]]
    if year == 0: return
    return datetime(year, month, day, hour, minute, second, 0)

logs = []
log_lengths, log_timedeltas = [], []
# compute log lengths (how many entries with non-zero sensor values?)
for filename in file_names:
    log_lines = []
    with open(os.path.join(LOG_PATH, filename)) as f:
        entryCount = 0
        incompleteCounter = 0
        _last_log_timestamp = None
        this_log_timedeltas = []
        for line in f.readlines():
            # start a new log per each time stamp found
            if entryCount == 0 and line[0] == "0" and string_to_datetime(line):
                log = {}
                log["datetime"] = string_to_datetime(line)
                entryCount = 1
            elif entryCount == 1 and line[0] == "1":
                log["TCP"] = [float(i) for i in line.split(';')[1:-1]]
                entryCount = 0 if sum(log["TCP"]) == 0 else 2
            elif entryCount == 2 and line[0] == "2":
                log["velocity"], log["tensionScaled"], log["tensionRaw"], log["E2"] = [float(i) for i in line.split(';')[1:-1]]
                entryCount = 0 if sum([float(i) for i in line.split(';')[1:-1]]) == 0 else 3
            elif entryCount == 3 and line[0] == "3":
                log["Axis"] = [float(i) for i in line.split(';')[1:-1]]
                entryCount = 0 if sum(log["Axis"]) == 0 else 4
            elif entryCount == 4 and line[0] == "4":
                log["Torque"] = [float(i) for i in line.split(';')[1:-1]]
                entryCount = 0 if sum(log["Torque"]) == 0 else 5
            # only add the log when all five entries are complete
            if entryCount == 5:
                log_lines.append(log)
                if _last_log_timestamp:
                    this_log_timedeltas.append(log["datetime"] - _last_log_timestamp)
                _last_log_timestamp = log["datetime"]
                entryCount = 0
            else:
                incompleteCounter += 1
        log_lengths.append((len(log_lines), incompleteCounter))
        sumtd = timedelta()
        for td in this_log_timedeltas:
            sumtd += td
        timeDeltaAverage = (sumtd.total_seconds()/len(this_log_timedeltas))
        log_timedeltas.append(timeDeltaAverage)
        print (f"{filename} : {len(log_lines)} complete log lines, {incompleteCounter} lines incomplete, {timeDeltaAverage:.2f} tdelta")
    logs.append(log_lines)

df = pd.DataFrame(dict(log_entries_count = [length[0] for length in log_lengths]))
fig = df.plot(title = "Number of Log Entries", labels = dict(mode="marker+line", index="sample #", value="number of entries"))
fig.show()

S01_0.txt : 14091 complete log lines, 85518 lines incomplete, 0.16 tdelta
S01_1.txt : 10392 complete log lines, 89217 lines incomplete, 0.18 tdelta
S01_2.txt : 9285 complete log lines, 90325 lines incomplete, 0.16 tdelta
S01_3.txt : 10545 complete log lines, 89064 lines incomplete, 0.18 tdelta
S01_4.txt : 14359 complete log lines, 85250 lines incomplete, 0.16 tdelta
S01_5.txt : 8288 complete log lines, 91322 lines incomplete, 0.22 tdelta
S01_6.txt : 8684 complete log lines, 90925 lines incomplete, 0.17 tdelta
S01_7.txt : 7361 complete log lines, 92249 lines incomplete, 0.22 tdelta
S01_8.txt : 9797 complete log lines, 89812 lines incomplete, 0.19 tdelta
S01_9.txt : 7814 complete log lines, 91796 lines incomplete, 0.21 tdelta


## 2: Fabrication Time

**On average, samples take 12 minutes to wind, 14 minutes to install FO/troubleshoot, 5 minutes in waiting.**

*Data log issue - sometimes points where velocity drop to zero are not documented, so adjacent frame IDs may have time stamps very far apart*

In [49]:
CUTOFF_VELOCITY = 0.001 # velocity under this threshold, the robot is considered stopped
CUTOFF_DURATION_FOR_PAUSE = 180 # minimum number of seconds to consider a "pause" 
MAX_VELOCITY = 0.08 # velocity beyond this threshold, robot is doing the initial PTP movement

long_pauses, dormant_durations, active_durations = [], [], []
for log_lines in logs:
    print (f"Sample {index} :")
    index = logs.index(log_lines)
    dormant_duration, long_pause = timedelta(), timedelta()
    _last_timestamp = log_lines[0]["datetime"]
    stopped = False
    
    for line in log_lines:
        if not stopped:
            ### deal with logging error where velocity drop to zero was not captured
            if (line["datetime"] - _last_timestamp).total_seconds() > CUTOFF_DURATION_FOR_PAUSE:
                long_pause += line["datetime"] - _last_timestamp
                print(f"     unexpected pause at {_last_timestamp} for ", (line["datetime"] - _last_timestamp))
            _last_timestamp = line["datetime"]
            ###
            if line["velocity"]<CUTOFF_VELOCITY:
                stopped = True
                last_timestamp = line["datetime"]
        else:
            if line["velocity"]>=CUTOFF_VELOCITY:
                stopped = False
                if (line["datetime"] - last_timestamp).total_seconds() > CUTOFF_DURATION_FOR_PAUSE:
                    long_pause += line["datetime"] - last_timestamp
                    print(f"     pause at {last_timestamp} for ", (line["datetime"] - last_timestamp))
                else:
                    dormant_duration += line["datetime"] - last_timestamp
    total_duration = log_lines[-1]["datetime"] - log_lines[0]["datetime"]
    dormant_durations.append(dormant_duration.total_seconds()/60)
    long_pauses.append(long_pause.total_seconds()/60)
    active_durations.append((total_duration - dormant_duration - long_pause).total_seconds()/60)
    print (f"---- total time", total_duration)

print (f"\naverage active winding time {(sum(active_durations)/len(active_durations)):.1f} minutes")
print (f"average time for long pause {(sum(long_pauses)/len(long_pauses)):.1f} minutes")
print (f"average dormant time {(sum(dormant_durations)/len(dormant_durations)):.1f} minutes")
    
# a = np.array([l/(d*6) for l, d in zip([length[0] for length in log_lengths], total_durations)])
b = np.array(active_durations)
c = np.array(dormant_durations)
d = np.array(long_pauses)
df = pd.DataFrame(dict(active_time = b, dormant_time = c, long_pauses = d))
fig0 = df.plot.bar(title = "Fabrication Time", labels = dict(index="sample #", value="minutes", variable="type"))
fig0.update_xaxes(type='category')
fig0.show()

Sample 9 :
     pause at 2021-06-11 19:46:33 for  0:05:09
     unexpected pause at 2021-06-11 19:46:33 for  0:05:09
     unexpected pause at 2021-06-11 20:00:41 for  0:10:46
---- total time 0:36:38
Sample 0 :
     unexpected pause at 2021-06-11 20:29:37 for  0:12:43
---- total time 0:31:48
Sample 1 :
     unexpected pause at 2021-06-11 21:11:00 for  0:07:46
---- total time 0:24:48
Sample 2 :
     unexpected pause at 2021-06-11 21:46:29 for  0:12:27
---- total time 0:31:49
Sample 3 :
     pause at 2021-06-11 18:20:55 for  0:05:24
     unexpected pause at 2021-06-11 18:20:55 for  0:05:24
     unexpected pause at 2021-06-11 18:27:14 for  0:11:04
---- total time 0:37:26
Sample 4 :
     unexpected pause at 2021-06-11 16:05:45 for  0:15:24
---- total time 0:30:37
Sample 5 :
     unexpected pause at 2021-06-11 16:53:40 for  0:08:30
---- total time 0:24:26
Sample 6 :
     unexpected pause at 2021-06-11 19:07:52 for  0:13:29
---- total time 0:27:00
Sample 7 :
     unexpected pause at 2021-06-11

## 3: Tension and TCP Velocity Plot

**For each sample there are two plots:**
- 3D plot: point size correlates to tension, color correlates to velocity
- 2D plot: timeline showing the changes in tension and velocity

In [66]:
LOG_TO_SHOW = 6

''' tension values of all samples in one graph '''

# plt.figure(figsize=(15,5))
# plt.title("tension of all samples")
# for i in range(len(logs)):    
#     tensionValues = [log["tensionRaw"] for log in logs[i]]
#     plt.plot(np.array(tensionValues), label = f"log {i}")
# plt.xlabel('log entries')
# plt.ylabel('tension (raw)')
# plt.legend(loc="upper right")
# plt.show()

''' velocity of all samples in one graph '''

# plt.figure(figsize=(15,5))
# plt.title("TCP velocity of all samples")
# for i in range(len(logs)):    
#     velocityValues = [log["velocity"] for log in logs[i]]
#     plt.plot(np.array(velocityValues), label = f"log {i}")
# plt.xlabel('log entries')
# plt.ylabel('velocity')
# plt.legend(loc="upper right")
# plt.show()

''' tension and velocity values of each individual sample '''

import plotly.express as px

from plotly.subplots import make_subplots
import plotly.graph_objects as go
from ipywidgets import widgets, Layout

# rendering issues when all the plots are in one cell
X_TICK_FREQUENCY = 200
CULL_DISTANCE = 280

fig = make_subplots(rows=1, cols=2, specs=[[{'type': 'xy'}, {'type': 'scene'}]], column_widths=[0.4, 0.6], 
                       horizontal_spacing = 0.05, vertical_spacing = 0.05,)
fig = go.FigureWidget(fig)

for i in range(LOG_TO_SHOW,LOG_TO_SHOW+1):
    tensionValues, velocityValues, tcpX, tcpY, tcpZ, ids = [], [], [], [], [], []
    unfilteredListTags, unfilteredListId, unfilteredTimeStamps =[], [], []
    tensionValuesUnfiltered, velocityValuesUnfiltered=[],[]
    _tcpX = [log["TCP"][0] for log in logs[i] if (log["velocity"]>CUTOFF_VELOCITY and log["velocity"]<MAX_VELOCITY)]
    avgX = sum(_tcpX)/len(_tcpX)
    for j in range(len(logs[i])):
        log = logs[i][j]
        unfilteredListId.append(j)
        tensionValuesUnfiltered.append(log["tensionRaw"])
        velocityValuesUnfiltered.append(log["velocity"])
        unfilteredTimeStamps.append(logs[i][j]["datetime"].strftime("@%H:%M:%S"))
        if abs(log["TCP"][0] - avgX) < CULL_DISTANCE and log["velocity"]>CUTOFF_VELOCITY and log["velocity"]<MAX_VELOCITY:
            tensionValues.append(log["tensionRaw"]*50)
            velocityValues.append(log["velocity"])
            tcpX.append(log["TCP"][0])
            tcpY.append(log["TCP"][1])
            tcpZ.append(log["TCP"][2])
            ids.append(f"ID:{j}")
            unfilteredListTags.append(1)
        else:
            unfilteredListTags.append(0)
    fig.update_layout(height=400, width=960, title_text=f"Sample {i} Tension and Velocity Plot", 
                      xaxis=dict(rangeslider=dict(visible=True)), 
                      margin=dict(l=10, r=10, b=50, t=50, pad=4 ))
    # 3D scatter graph
    fig.append_trace(go.Scatter3d(showlegend=True, name = "", #hovertext = ids, 
                        x=tcpX, y=tcpY, z=tcpZ, mode='markers',
                        customdata = list(zip([t/50 for t in tensionValues], velocityValues, ids)), 
                        hovertemplate='<b>%{customdata[2]}</b><br>T=%{customdata[0]:.2f}, V=%{customdata[1]:.2f}',
                        marker=dict(size=tensionValues, color=velocityValues, opacity=0.8, sizemode="diameter")), row=1, col=2)
    fig.update_traces(marker=dict(line=dict(width=0)))
    # 2D line graph
    fig.append_trace(go.Scatter(x=unfilteredListId, y=tensionValuesUnfiltered, name='tension'), row=1, col=1)
    fig.append_trace(go.Scatter(x=unfilteredListId, y=velocityValuesUnfiltered, name='velocity',hovertext = unfilteredTimeStamps), row=1, col=1)
    fig.update_yaxes(title_text="tension / velocity", row=1, col=1)
    fig.update_xaxes(title_text="frame ID", row=1, col=1)
    fig.update_layout(hovermode='x unified', legend=dict( yanchor="bottom", y=-.5, xanchor="right", x=0.7))
    fig.show()
    

In [67]:
DEFAULT_LOG_ID = 0

sample_selector = widgets.Dropdown(options= [str(i) for i in range(len(logs))], disabled=False,
    value=str(DEFAULT_LOG_ID), layout=Layout(width='180px'), description='sample:',
)

def response1(change):
    if sample_selector.value:
        range_slider.max = len(logs[int(sample_selector.value)])
sample_selector.observe(response1, names="value")

range_slider = widgets.IntRangeSlider(
    value=[0, len(logs[DEFAULT_LOG_ID])], min=0, max=len(logs[DEFAULT_LOG_ID]), step=1, continuous_update=False,
    description='time frame:', readout_format='d', layout=Layout(width='620px')
)

button = widgets.Button(
    description='Compute',
    disabled=False,
    button_style='info',
    tooltip='Compute graph for selected sample', icon='rocket'
)
def response2(_button):
    with fig.batch_update():
        updatePlot(int(sample_selector.value), int(range_slider.value[0]), int(range_slider.value[1]), fig)
button.on_click(response2)

def updatePlot(log_id, start, end, _fig):
    tensionValues, velocityValues, tcpX, tcpY, tcpZ, ids = [], [], [], [], [], []
    unfilteredListTags, unfilteredListId, unfilteredTimeStamps = [], [], []
    velocityValuesUnfiltered, tensionValuesUnfiltered = [], []
    sizeMultiplier = 50
    for j in range(start, end): #len(logs[log_id])
        log = logs[log_id][j]
        unfilteredListId.append(j)
        tensionValuesUnfiltered.append(log["tensionRaw"])
        velocityValuesUnfiltered.append(log["velocity"])
        unfilteredTimeStamps.append(str(j) + logs[i][j]["datetime"].strftime(" (%H:%M:%S)"))
        if 1:
#         if abs(log["TCP"][0] - avgX) < CULL_DISTANCE and log["velocity"]>CUTOFF_VELOCITY and log["velocity"]<MAX_VELOCITY:
            tensionValues.append(log["tensionRaw"]*sizeMultiplier)
            velocityValues.append(log["velocity"])
            tcpX.append(log["TCP"][0])
            tcpY.append(log["TCP"][1])
            tcpZ.append(log["TCP"][2])
            ids.append(f"ID:{j}")
            unfilteredListTags.append(1)
        else:
            unfilteredListTags.append(0)
    _fig.data[0].x = tcpX
    _fig.data[0].y = tcpY
    _fig.data[0].z = tcpZ
#     _fig.data[0].hovertext = ids
    _fig.data[0].customdata = list(zip([t/50 for t in tensionValues], velocityValues, ids))
    _fig.data[0].marker.color = velocityValues
    _fig.data[0].marker.size = tensionValues
    _fig.data[1].x = unfilteredListId
    _fig.data[1].y = tensionValuesUnfiltered
    _fig.data[2].x = unfilteredListId
    _fig.data[2].y = velocityValuesUnfiltered
    _fig.data[2].hovertext = unfilteredTimeStamps
    _fig.layout.title.text =f"Sample {log_id} Tension and Velocity Plot"

container = widgets.HBox(children=[sample_selector, range_slider, button])

# def response(change):
#     if range_slider.value:
# #         print (f"selected range: {range_slider.value} for sample {sample_selector.value}")
#         print (fig.data[2])
# range_slider.observe(response, names="value")
# container

widgets.VBox([container, fig])

*To batch export individual graphs, swap out list range below.*

In [8]:
# START_RANGE = 1 #0
# END_RANGE = 2 #len(logs)
# for i in range(START_RANGE,END_RANGE):
#     tensionValues, velocityValues, tcpX, tcpY, tcpZ, ids = [], [], [], [], [], []
#     unfilteredListTags, unfilteredListId, unfilteredTimeStamps =[], [], []
#     _tcpX = [log["TCP"][0] for log in logs[i] if (log["velocity"]>CUTOFF_VELOCITY and log["velocity"]<MAX_VELOCITY)]
#     avgX = sum(_tcpX)/len(_tcpX)
#     for j in range(len(logs[i])):
#         log = logs[i][j]
#         unfilteredListId.append(j)
#         tensionValuesUnfiltered.append(log["tensionRaw"])
#         velocityValuesUnfiltered.append(log["velocity"])
#         unfilteredTimeStamps.append(logs[i][j]["datetime"].strftime("@%H:%M:%S"))
#         if abs(log["TCP"][0] - avgX) < CULL_DISTANCE and log["velocity"]>CUTOFF_VELOCITY and log["velocity"]<MAX_VELOCITY:
#             tensionValues.append(log["tensionRaw"]*50)
#             velocityValues.append(log["velocity"])
#             tcpX.append(log["TCP"][0])
#             tcpY.append(log["TCP"][1])
#             tcpZ.append(log["TCP"][2])
#             ids.append(f"Frame {j}")
#     df = pd.DataFrame(dict(tension_raw = tensionValues, tcp_x = tcpX, tcp_y = tcpY, tcp_z =tcpZ, ids = ids, velocity = velocityValues))
#     fig3 = px.scatter_3d(df, x="tcp_x", y = "tcp_y", z = "tcp_z", color = "velocity", size ="tension_raw", 
#                          size_max = 35, hover_name  = "ids")
#     fig3.update_traces(marker=dict(line=dict(width=0)))
#     fig3.update_layout(xaxis=dict(rangeslider=dict(visible=True)))
#     fig3.show()
    
#     df = pd.DataFrame(dict(tension_raw = tensionValuesUnfiltered, velocity = velocityValuesUnfiltered))
#     fig2 = df.plot(title = f"Tension and TCP Velocity for Sample {i}", labels = dict(index = "timestamps"))
#     fig2.update_xaxes(tickmode = "array", tickvals = np.arange(0, len(timeStamps), X_TICK_FREQUENCY).astype(int), \
#                       ticktext = timeStamps[::X_TICK_FREQUENCY], tickangle=45)
#     fig2.show()

## 4: Tension Velocity Comparison for All Samples

**At similar TCP velocity, sample 4 has the highest tension, while sample 5 the lowest.**

**Average velocity of all samples is quite evenly distributed, at 0.048.**

**Average tension of all samples varies quite a bit.**

In [9]:
maxTension, medTension, avgTension, sdTension = [], [], [], []
maxVelocity, medVelocity, avgVelocity, sdVelocity = [], [], [], []
for i in range(len(logs)):    
    activeTensionValues = [log["tensionRaw"] for log in logs[i] if (log["velocity"]>CUTOFF_VELOCITY and log["velocity"]<MAX_VELOCITY)]
    activeTensionValues.sort()
    mid = len(activeTensionValues) // 2
    medTension.append((activeTensionValues[mid] + activeTensionValues[~mid]) / 2)
    maxTension.append(max(activeTensionValues))
    avgTension.append(sum(activeTensionValues)/len(activeTensionValues))
    sdTension.append(math.sqrt( sum([math.pow((t-avgTension[i]), 2) for t in activeTensionValues]) /len(activeTensionValues)))
    
    activeVelocityValues = [log["velocity"] for log in logs[i] if (log["velocity"]>CUTOFF_VELOCITY and log["velocity"]<MAX_VELOCITY)]
    activeVelocityValues.sort()
    mid = len(activeVelocityValues) // 2
    medVelocity.append((activeVelocityValues[mid] + activeVelocityValues[~mid]) / 2)
    maxVelocity.append(max(activeVelocityValues))
    avgVelocity.append(sum(activeVelocityValues)/len(activeVelocityValues))
    sdVelocity.append(math.sqrt(sum([math.pow((v-avgVelocity[i]), 2) for v in activeVelocityValues])/len(activeVelocityValues)))

df1 = pd.DataFrame(dict(max_tension = maxTension, median_tension = medTension, average_tension = avgTension))
df2 = pd.DataFrame(dict(max_velocity = maxVelocity, median_velocity = medVelocity, average_velocity = avgVelocity))
fig1 = df1.plot.bar(title = f"Tension Values for All Samples (when velocity > {CUTOFF_VELOCITY})", 
                    labels = dict(index="sample #", value="value", variable="variable"), barmode='group')
fig2 = df2.plot.bar(title = f"Velocity for All Samples (when velocity > {CUTOFF_VELOCITY})", 
                    labels = dict(index="sample #", value="value", variable="variable"), barmode='group')
fig1.update_xaxes(type='category')
fig2.update_xaxes(type='category')
fig1.show()
fig2.show()

## 5: Tension - Velocity Histogram

**Tension has a proportional relationship to velocity, especially up to velocity of 0.03.**

In [10]:
tensionValues, velocityValues, tags = [], [], []
for i in range(len(logs)):
    tensionValues += [log["tensionRaw"] for log in logs[i] if (log["velocity"]>CUTOFF_VELOCITY and log["velocity"]<MAX_VELOCITY)]
    velocityValues += [log["velocity"] for log in logs[i] if (log["velocity"]>CUTOFF_VELOCITY and log["velocity"]<MAX_VELOCITY)]
    tags += [f"sample{i}" for log in logs[i] if (log["velocity"]>CUTOFF_VELOCITY and log["velocity"]<MAX_VELOCITY)]

df = pd.DataFrame(dict(tension=tensionValues, velocity = velocityValues, ID = tags))
# fig = df.plot.scatter(title=f"Tension and TCP Velocity Plot for All Samples (when velocity > {CUTOFF_VELOCITY})", 
#                         x="velocity", y="tension", hover_data=["ID"], color = "ID")
fig1= df.hist(title=f"Tension and TCP Velocity Histogram for All Samples Overlaid(when velocity > {CUTOFF_VELOCITY})", 
                        y="tension", x="velocity", color = "ID", nbins=20, histfunc='avg', barmode='group') #barmode='overlay')
# fig.update_traces(opacity=0.5)
fig1.show()